In [1]:
import numpy as np
import pandas as pd
from pandas_profiling import ProfileReport

In [2]:
# Пути к директориям и файлам
# input_train
TRAIN_DATASET_PATH = 'train.csv'
# input_test
TEST_DATASET_PATH = 'test.csv'
# output
PREP_DATASET_PATH = 'sample_submission.csv'

In [3]:
def print_null_value_counts(col_nm):
    print( f"miss_count: \t{df[col_nm].isnull().sum()} ")
    print( '--------------------\nValues\t  count\n--------------------')
    print( f"{df[col_nm].value_counts()}")
    

In [4]:
df = pd.read_csv(TRAIN_DATASET_PATH)
df.head()

Home Ownership  Annual Income Years in current job  Tax Liens  \
0       Own Home       482087.0                  NaN        0.0   
1       Own Home      1025487.0            10+ years        0.0   
2  Home Mortgage       751412.0              8 years        0.0   
3       Own Home       805068.0              6 years        0.0   
4           Rent       776264.0              8 years        0.0   

   Number of Open Accounts  Years of Credit History  Maximum Open Credit  \
0                     11.0                     26.3             685960.0   
1                     15.0                     15.3            1181730.0   
2                     11.0                     35.0            1182434.0   
3                      8.0                     22.5             147400.0   
4                     13.0                     13.6             385836.0   

   Number of Credit Problems  Months since last delinquent  Bankruptcies  \
0                        1.0                           NaN           1.0   
1                        0.0                           NaN           0.0   
2                        0.0                           NaN           0.0   
3                        1.0                           NaN           1.0   
4                        1.0                           NaN           0.0   

              Purpose        Term  Current Loan Amount  \
0  debt consolidation  Short Term           99999999.0   
1  debt consolidation   Long Term             264968.0   
2  debt consolidation  Short Term           99999999.0   
3  debt consolidation  Short Term             121396.0   
4  debt consolidation  Short Term             125840.0   

   Current Credit Balance  Monthly Debt  Credit Score  Credit Default  
0                 47386.0        7914.0         749.0               0  
1                394972.0       18373.0         737.0               1  
2                308389.0       13651.0         742.0               0  
3                 95855.0       11338.0         694.0               0  
4                 93309.0        7180.0         719.0               0

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7500 entries, 0 to 7499
Data columns (total 17 columns):
 #   Column                        Non-Null Count  Dtype  
---  ------                        --------------  -----  
 0   Home Ownership                7500 non-null   object 
 1   Annual Income                 5943 non-null   float64
 2   Years in current job          7129 non-null   object 
 3   Tax Liens                     7500 non-null   float64
 4   Number of Open Accounts       7500 non-null   float64
 5   Years of Credit History       7500 non-null   float64
 6   Maximum Open Credit           7500 non-null   float64
 7   Number of Credit Problems     7500 non-null   float64
 8   Months since last delinquent  3419 non-null   float64
 9   Bankruptcies                  7486 non-null   float64
 10  Purpose                       7500 non-null   object 
 11  Term                          7500 non-null   object 
 12  Current Loan Amount           7500 non-null   float64
 13  Cur

In [6]:
# Анализ значений с помощью ProfileReport(df)
#report = ProfileReport(df)
#report

In [7]:
print( df['Home Ownership'].value_counts() )

Home Mortgage    3637
Rent             3204
Own Home          647
Have Mortgage      12
Name: Home Ownership, dtype: int64


In [8]:
#pd.get_dummies(df['Home Ownership'], prefix='Home Ownership')

In [9]:
# Объединим два значения в одно Иметь ипотеку и ипотека на жилье 
df.loc[df['Home Ownership'] == 'Have Mortgage', 'Home Ownership'] = 'Home Mortgage'
print( df['Home Ownership'].value_counts() )

Home Mortgage    3649
Rent             3204
Own Home          647
Name: Home Ownership, dtype: int64


In [10]:
#Annual Income - Годовой доход имеется занчительное число пропусков Missing (%)	20.8%
low_lim = df['Annual Income'].describe()['25%']
hi_lim = df['Annual Income'].describe()['75%']
n_size = df['Annual Income'].isnull().sum()
r_data = np.random.randint( low=low_lim, high=hi_lim, size=n_size ).astype(np.float64)
miss_data = pd.DataFrame( 
    data = r_data, 
    index = df.loc[df['Annual Income'].isnull(), 'Annual Income'].index,
    columns = ['Annual Income',]
) 
miss_data

Annual Income
5         1583277.0
8         1297751.0
9         1187322.0
10        1065245.0
16        1271844.0
...             ...
7482       957690.0
7492      1207208.0
7494      1164435.0
7498      1551412.0
7499      1082825.0

[1557 rows x 1 columns]

In [11]:
df.loc[df['Annual Income'].isnull(), 'Annual Income'] = miss_data

In [12]:
# Years in current job Missing	371 Missing (%)	4.9%
col_nm = 'Years in current job'
print_null_value_counts(col_nm)

miss_count: 	371 
--------------------
Values	  count
--------------------
10+ years    2332
2 years       705
3 years       620
< 1 year      563
5 years       516
1 year        504
4 years       469
6 years       426
7 years       396
8 years       339
9 years       259
Name: Years in current job, dtype: int64


In [13]:
cat_count = 5
assert cat_count < len(df[col_nm].value_counts().index.tolist())

lst_vals = df[col_nm].value_counts().head(cat_count).index.tolist()
cnt_vals = np.array(df[col_nm].value_counts().head(cat_count).values.tolist())
cnt_vals = cnt_vals/len(df)
add_val = (1.0-sum(cnt_vals))/cat_count
cnt_vals += add_val
#print(lst_vals, cnt_vals, sum(cnt_vals))
#print( np.random.choice(a=lst_vals, p=cnt_vals, size=20 ) )

r_data = np.random.choice(a=lst_vals, p=cnt_vals, size=df[col_nm].isnull().sum() ) 
miss_data = pd.DataFrame( 
    data = r_data, 
    index = df.loc[df[col_nm].isnull(), col_nm].index,
    columns = [col_nm,]
) 
miss_data

df.loc[df[col_nm].isnull(), col_nm] = miss_data


In [14]:
# достаточно много категорий уменьшим до 4х
import re
prog = re.compile(r"(\b\d{1,2})")

def rule(str):
    fs = int(prog.search(str).group(0))
    if fs >8:
        return 3
    elif fs>5:
        return 2
    elif fs >2:
        return 1
    return 0

df['INT Years in current job'] = df.apply(lambda x: rule(x[col_nm]), axis =  1)

# values = df['Years in current job'].value_counts().index
# prog = re.compile(r"(\b\d{1,2})")
# for str in values:
#     fs = int(prog.search(str).group(0))
#     if fs >8:
#         print(f' {str} --> {3}' )
#     elif fs>5:
#         print(f' {str} --> {2}' )
#     elif fs >2:
#         print(f' {str} --> {1}' )
#     else:
#         print(f' {str} --> {0}' )


In [15]:
# CHECK IT Years in current job Missing	371 Missing (%)	4.9%
print_null_value_counts(col_nm)

miss_count: 	0 
--------------------
Values	  count
--------------------
10+ years    2479
2 years       757
3 years       683
< 1 year      618
5 years       570
1 year        504
4 years       469
6 years       426
7 years       396
8 years       339
9 years       259
Name: Years in current job, dtype: int64


In [16]:
# Налоговые залоги Tax Liens 0- 7  причем 95% - 0 максимум 7 наверное можно сделать несколько градаций 
# отработать выбросы и перевести в int
col_nm = 'Tax Liens'
print_null_value_counts(col_nm)

miss_count: 	0 
--------------------
Values	  count
--------------------
0.0    7366
1.0      83
2.0      30
3.0      10
4.0       6
5.0       2
6.0       2
7.0       1
Name: Tax Liens, dtype: int64


In [17]:
df.loc[df[col_nm] > 3.0, col_nm] = 3.0
df[col_nm].astype(np.uint8)

print_null_value_counts(col_nm)

miss_count: 	0 
--------------------
Values	  count
--------------------
0.0    7366
1.0      83
2.0      30
3.0      21
Name: Tax Liens, dtype: int64


In [18]:
# Maximum Open Credit Максимальный открытый кредит отрезать выбросы
col_nm = 'Maximum Open Credit'
print_null_value_counts(col_nm)

miss_count: 	0 
--------------------
Values	  count
--------------------
0.0          65
319110.0      5
334796.0      3
607046.0      3
294030.0      3
             ..
534600.0      1
1026124.0     1
77066.0       1
780164.0      1
350768.0      1
Name: Maximum Open Credit, Length: 6963, dtype: int64


In [19]:
df.loc[df[col_nm] > df[col_nm].quantile(q=0.95), col_nm] = df[col_nm].quantile(q=0.98)
print_null_value_counts(col_nm)

miss_count: 	0 
--------------------
Values	  count
--------------------
2448540.6    375
0.0           65
319110.0       5
727958.0       3
334796.0       3
            ... 
951896.0       1
455730.0       1
1528560.0      1
521268.0       1
372658.0       1
Name: Maximum Open Credit, Length: 6592, dtype: int64


In [20]:
# Number of Credit Problems - Количество проблем с кредитованием 0-1-2-3 и более
col_nm = 'Number of Credit Problems'
print_null_value_counts(col_nm)

miss_count: 	0 
--------------------
Values	  count
--------------------
0.0    6469
1.0     882
2.0      93
3.0      35
4.0       9
5.0       7
6.0       4
7.0       1
Name: Number of Credit Problems, dtype: int64


In [21]:
df.loc[df[col_nm] > 4.0, col_nm] = 4.0
df[col_nm].astype(np.uint8)

print_null_value_counts(col_nm)

miss_count: 	0 
--------------------
Values	  count
--------------------
0.0    6469
1.0     882
2.0      93
3.0      35
4.0      21
Name: Number of Credit Problems, dtype: int64


In [22]:
# Months since last delinquent Missing	4081 Missing (%)	54.4%
df = df.drop(columns='Months since last delinquent')

In [23]:
# Bankruptcies Банкротства 0 - 1 - 2 и более 
col_nm = 'Bankruptcies'
print_null_value_counts(col_nm)

miss_count: 	14 
--------------------
Values	  count
--------------------
0.0    6660
1.0     786
2.0      31
3.0       7
4.0       2
Name: Bankruptcies, dtype: int64


In [24]:
lst_vals = df[col_nm].value_counts().index.tolist()
cnt_vals = np.array(df[col_nm].value_counts().values.tolist())
cnt_vals = cnt_vals/len(df)
add_val = (1.0-sum(cnt_vals))/len(lst_vals)
cnt_vals += add_val

r_data = np.random.choice(a=lst_vals, p=cnt_vals, size=df[col_nm].isnull().sum() ) 
miss_data = pd.DataFrame( 
    data = r_data, 
    index = df.loc[df[col_nm].isnull(), col_nm].index,
    columns = [col_nm,]
) 
miss_data

df.loc[df[col_nm].isnull(), col_nm] = miss_data

In [25]:
print_null_value_counts(col_nm)

miss_count: 	0 
--------------------
Values	  count
--------------------
0.0    6672
1.0     788
2.0      31
3.0       7
4.0       2
Name: Bankruptcies, dtype: int64


In [26]:
# Current Loan Amount Текущая сумма кредита  99999999	870	11.6% непонятно - выборос чем его заменить?
col_nm = 'Current Loan Amount'
print_null_value_counts(col_nm)

miss_count: 	0 
--------------------
Values	  count
--------------------
99999999.0    870
89298.0         6
218064.0        6
216106.0        5
270226.0        5
             ... 
490006.0        1
404756.0        1
194414.0        1
420376.0        1
33792.0         1
Name: Current Loan Amount, Length: 5386, dtype: int64


In [27]:
lst_vals = df[col_nm].value_counts().index.tolist()
replace_val = lst_vals[0]
lst_vals = lst_vals[1:]
cnt_vals = np.array(df[col_nm].value_counts().values.tolist())
sz = cnt_vals[0]
cnt_vals = cnt_vals[1:]
cnt_vals = cnt_vals/len(df)
add_val = (1.0-sum(cnt_vals))/len(lst_vals)
cnt_vals += add_val

r_data = np.random.choice(a=lst_vals, p=cnt_vals, size=sz ) 
miss_data = pd.DataFrame( 
    data = r_data, 
    index = df.loc[df[col_nm]==replace_val, col_nm].index,
    columns = [col_nm,]
) 
#miss_data
#print (miss_data.head()) 
df.loc[df[col_nm]==replace_val, col_nm] = miss_data

In [28]:
print_null_value_counts(col_nm)

miss_count: 	0 
--------------------
Values	  count
--------------------
218064.0    7
223322.0    7
216106.0    6
225830.0    6
89298.0     6
           ..
197208.0    1
783244.0    1
449768.0    1
218768.0    1
33792.0     1
Name: Current Loan Amount, Length: 5385, dtype: int64


In [29]:
# Current Credit Balance
# col_nm = 'Current Credit Balance'
# print_null_value_counts(col_nm)

In [30]:
#df.loc[df[col_nm] > df[col_nm].quantile(q=0.95), col_nm].value_counts()

In [31]:
# df.loc[df[col_nm] > df[col_nm].quantile(q=0.95), col_nm] = df[col_nm].quantile(q=0.98)
# print_null_value_counts(col_nm)

In [32]:
# Credit Score - кредитный рейтинг Missing	1557 Missing (%)	20.8%
df = df.drop(columns='Credit Score')

In [33]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7500 entries, 0 to 7499
Data columns (total 16 columns):
 #   Column                     Non-Null Count  Dtype  
---  ------                     --------------  -----  
 0   Home Ownership             7500 non-null   object 
 1   Annual Income              7500 non-null   float64
 2   Years in current job       7500 non-null   object 
 3   Tax Liens                  7500 non-null   float64
 4   Number of Open Accounts    7500 non-null   float64
 5   Years of Credit History    7500 non-null   float64
 6   Maximum Open Credit        7500 non-null   float64
 7   Number of Credit Problems  7500 non-null   float64
 8   Bankruptcies               7500 non-null   float64
 9   Purpose                    7500 non-null   object 
 10  Term                       7500 non-null   object 
 11  Current Loan Amount        7500 non-null   float64
 12  Current Credit Balance     7500 non-null   float64
 13  Monthly Debt               7500 non-null   float

In [34]:
report = ProfileReport(df)
report